In [1]:
#%matplotlib notebook
from z_utils.Tracker import Tracker
from z_utils.init_detector_05 import *
from DiffuseMap import *
import socket
import json

In [ ]:
class ROS_Linker:
    def __init__(self):
        self.CaptureObject=None
        self.list_params=None
        self.video_out=None
        self.Tracker=None
        self.diffuse_map = None

    def initParams(self):
        print('initParam...')

        path_in = 'video_frames/video_20/' #Папка в которой лежат либо фотографии либо видео
        file_name = ''   #Для папки с фоторгафиями оставляем пустой. Для видео пишем ТОЛЬКО название видео.
        video_name = file_name + '.mp4'
        path_out = './output/'
        clear_dir_00(path_out) #Очищаем всю папку path_out
        path_out_for_DM_images = path_out + path_in + '/'  # куда складывать картинки с диффузной картой

        #Сохранение для папки с кадрами.
        if len(file_name) == 0:
            name = path_in
            ext = '.mp4'
            self.video_in = path_in + file_name + '/'
            self.video_out = path_out + name + '/' + name[:-1] + ext
        #Сохранение для видео.
        else:
            name = path_in
            ext = '.mp4'
            self.video_in = path_in + video_name
            self.video_out = path_out + name + '/' + file_name + ext
            

        if not os.path.exists(path_out_for_DM_images):
            os.makedirs(path_out_for_DM_images)

        clear_dir_00(path_out_for_DM_images) # Очищаем папку куда сложили дифф карту
        clear_dir_00('save_fig/')

        print('video_in', self.video_in)
        print('video_out', self.video_out)
        print('path_out_for_DM_images', path_out_for_DM_images)


        input_type_flag = 3  # Тип входных данных:0 - видео, 1 - папка с файлами, 2 - rtsp-поток (тут веб-камера сейчас), 3 - ftp-поток (не реализовано), 4 - ROS
        flag_cut_and_save_objects = 0  # вырезаем объекты в ббоксах
        flag_save_tr_mat = 0  # собираем ли траектории в мат
        flag_debug = 0  # надо ли сохранять картинки нарезанные. Не используется
        ########################################################
        p_opt_flow = 0.99  # 0- идем по предикт, 1- идем по оптикал флоу
        ########### Настраиваем тут предиктор ##################
        predictor_type = 4  # 0 - yolo, 1 - detectron2 (cadet), 2 - detectron2 (pedet), 3 - face_detection, 4 - facenet_pytorch
        ########################################################
        video_adapter = 1 # Выбор видеоадаптера: 0 - CPU, 1 - GPU
        ########################################################
        add_holistic = 0 # 0 - выключить скелет, 1 - включить скелет
        ########################################################
        show_3Dpoints_holistic = 0 # 1 - Будет рисоваться скелет с фрагментами в папке save_fig 
        ########################################################
        show3D_one_points = 0 # 1 - Будет рисоваться только 1 точка головы с фрагментами в папке save_fig 
        ########################################################
        show_BBOX = 0 # Флаг для отрисовки ББокса и превью.
        ########################################################
        show_diffusion = 0 # 0 - выключена дифф мапа, 1 - включена на запись
        ########################################################

        thr_confidence = 0.99 #Отвечает за удаления ложных айдишников

        #Используем предиктор 4 - фейснет пайторч
        main_predictor = None
        if predictor_type == 0:
            main_predictor = detector_cocos(thr_confidence)
        elif predictor_type == 1:
            main_predictor = detector_detectron_cadet(model='cadet')
        elif predictor_type == 2:
            main_predictor = detector_detectron_cadet(model='pedet')
        elif predictor_type == 3:
            main_predictor = detector_detectron_cadet()
        elif predictor_type == 4:
            main_predictor = detector_facenet_pytorch(thr_confidence, video_adapter)
        else:
            pass
        
        #Для потока в вебкамеры, заменяем self.video_in на 0. Сохранять фото
        if input_type_flag == 2:
            self.video_in = 0
            self.video_out = path_out + path_in + 'rtsp_video' + ext
        if input_type_flag == 3:
            self.video_in = "udp://@172.16.119.221:1111"
            self.video_out = path_out + path_in + 'rtsp_video' + ext
        
            
        dscr_TL_00 = descr_745_init(11)  # 11 - фейснет
        ####################################

        self.list_params = {
            'path_out': path_out,
            'dscr_TL_00': dscr_TL_00, #Выбор дескриптора. Используем 11 - Facenet, получаеим вектора
            'detector_01': main_predictor,  # детектор для распознавалки объектов
            'detector_02': main_predictor,  # predictor_010,  # ела для распознавалки объектов
            'double_detect_flag': 0,  # если 1, то в фоновом режиме без трека распознаем объекты предиктором 2
            'input_type_flag': input_type_flag, # Выбор модели загрузки файлов/видео/вебкамера
            'predictor_type': predictor_type, #Используем предиктор фейснет_пайторч
            'diffuse_map': self.diffuse_map, 
            'flag_cut_and_save_objects': flag_cut_and_save_objects,
            'flag_save_tr_mat': flag_save_tr_mat,
            'DM_save': None,
            'flag_debug': flag_debug,
            'add_holistic': add_holistic, #Включить скелет или нет
            'path_out_for_DM_images': path_out_for_DM_images,
            'show_diffusion': show_diffusion, #Флаг для дифф карты
            'show_3Dpoints_holistic': show_3Dpoints_holistic, #флаг для 3Д точек
            'show3D_one_points': show3D_one_points, #Флаг для 3Д одной точки
            'show_BBOX': show_BBOX,
            'video_adapter': video_adapter, #Флаг выбора CPU/GPU
            'quality_width': 640, #Флаг выбора качества
            'resize_coef': 16/9, #Формат изображения
            'compensaition_index' : 8,
            'cannals_hist': 0,  ### 0- гистограмма hue для идентификации объекта, 2- гистограмма яркости

            'flag_classify_traj': 3,  ### классификатор траекторий: 0 - CNN, 1 - lstm, 2- mll, 3 - simple classify
            'path_to_w_classify_traj': 'classify_trajs\\InpOut001_mll_weights_25eps.h5',
            # None, # путь к весам классификатора траекторий
            'flag_prediction': 0,  ### lstm обучена не на том=>  флаг=0 #предсказатель траектории
            'path_to_prediction': None,  # 'q00_person.h5'# путь к весам предсказателя траекторий #

            'thr_color_features': 0.7, #Порог отвечает за сравнение косинусных расстояний. Сравнивает расстояния больше порога
            'check_period': 5,  #Отвечает за количество списков с векторами # forget_horizont_vert #30 - хорошо работает
            'debug_visu': 1,
            'border_edge': 5,  # относительно каких границ ищем новые объекты, used in add_new_object
            'r_edge': 1,  # относительно   границ ищем новые объекты  1- внутри области, -1 снаружи, used in add_new_object

            'l_forget_history': 15,
            'confidence_trashhold': 0.999, #отвечает за то, чтобы добавлялись в список векторизаций только хорошие детекции

            'manual_thr_radius': 2000, # %%%%% Радиус для поиска лица %%%%%

            'threshold': [0.6, 0.7, 0.7],  # three steps's threshold
            'factor': 0.709,  # scale factor 0.709
            'margin': 44, #НЕ ИСПОЛЬЗУЕТСЯ для фейснет_пайторч
            'thr_measure_hue_optflow2predict': None,
            'thr_add_new': 200, # Радиус. Используется в add_new_object
            'thr_correct_opt_flow': p_opt_flow * 350,
            ### если OF скакнуло от предикта больше чем thr_correct_opt_flow, верим предикту
            'prefix_ind_save_0': 10500000,
            'p_opt_flow': p_opt_flow,  # 0- идем по предикт, 1- идем по оптикал флоу
            'start_ind': 1,
            'class_to_interest': np.array(range(10)), #Не очень понял
            'debug_count': -15  # 25*60*5  # 5 минут
        }
        # self.video_out = path_out + filename_out
        #На шаффл История - 10. Чек период - 20
        #На сортированный. История - 10. Чек период - 10

    def init_diffuse_map(self):
        self.diffuse_map = DiffuseMap('pickles/facenet_pytorch.pickle', 0.8, True, 'pickles/DM_vector512.pickle')


    def initCaptureObject(self):
        print('initCaptureObj...')
        self.CaptureObject = Caption_Class_01(self.video_in, self.list_params['input_type_flag'], 1920) #Качество для вебки

    def initTracker(self):
        print('initTracker...')
        self.Tracker= Tracker(self.CaptureObject,self.video_out,self.list_params)
        self.Tracker.InitTracker()

    def TrackImage(self,image=None):
        if self.list_params['input_type_flag'] == 4:
            self.UpdateImage(image)

        return self.Tracker.TrackImage()
    
    def ShutdownTracker(self): #Функция отвечает за сохранение видео
        
        return self.Tracker.ShutdownTracker()
    
    def UpdateImage(self,image):
        self.CaptureObject.updateImageROS(image)
       

    
linker=ROS_Linker()#инициализируем класс
#Сначала инициализируем параметры, связанных с путями до файлов. Затем часть кода для сохранения файлов, если берем видео, или берем папку с файлами
#Далее идет часть кода, где происходит выбор флагов для определенных компонентов кода. Выбираем предиктор, используем фейснет_пайторч. 
#Для потока с вебкамеры заменяем self.video_in. Далее происходит выбор дескриптора, для получения векторизации
#Далее загружаем много параметров, которые используются в коде. Описание есть у всех. Функции далее описаны ниже.
linker.init_diffuse_map()#инициализируем дифф. мапу
linker.initParams()#загружаем все параметры
linker.initCaptureObject()#Загружаем путь к входному видео или в зависимости от флага, переключаемся на камеру
linker.initTracker()

HOST, PORT = "172.16.119.227", 11309
sock = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)

while linker.CaptureObject.isOpened():
    track_result = linker.TrackImage()#Запуск трекера
    result  = '{"objects":['
    is_first = True
    try:
        for i in track_result:
            if i['owned'][-1] > 0.5 and i['age'] > 3:

                if not is_first:
                    result += ', '
                else:
                    is_first = False
                result += '{{ "id": "{}", "x": {}, "y": {}, "z": {}, "name": "{}"}}'.format(i['id'], round(i['3D_points'][0], 4), round(i['3D_points'][1], 4), round(i['3D_points'][2], 4), 'human')

                # result[i['id']] = {'x': round(i['3D_points'][0], 4), 'y': round(i['3D_points'][1], 4), 'z': round(i['3D_points'][2], 4)}
            elif i['owned'][-1] < 0.5 and i['age'] > 3:

                if not is_first:
                    result += ', '
                else:
                    is_first = False
                result += '{{ "id": "{}", "x": {}, "y": {}, "z": {}, "name": "{}"}}'.format(i['id'], round(i['3DV_lost'][0], 4), round(i['3DV_lost'][1], 4), round(i['3DV_lost'][2], 4), 'human')

                # result[i['id']] = {'x': round(i['3DV_lost'][0], 4), 'y': round(i['3DV_lost'][1], 4), 'z': round(i['3DV_lost'][2], 4)}

    except:
        pass
        # data = json.dumps(result)


    result += ']}'
    #data = json.dumps(result)
    data = result
    sock.sendto(bytes(data + "\n", "utf-8"), (HOST, PORT))
    #sock.sendto(bytes(data, "utf-8"), (HOST, PORT))
    print("Sent:{}".format(data))       
    #Что мы получаем в track_result:
    #age - Сколько фрагментов этот человек есть в кадре. age_lost - Сколько кадров фрагмента нет в кадре
    #id - Номер задетекченного человека. #history - Записывает центр Ббокса в каждом кадре объекта.
    #history_X - тоже самое. owned - записывает 1 - если объект есть в кадре, 0 - если пропал из кадра.
    #Используется для обновление истории. Если много нулей, то пропадает из детекта человек.
    #holistic - Записывает 3д точки скелета объекта. descriptor_ - Записывает 512 значений, используется для детекта лица.
    #descriptor_ - векторизация каждого id в каждом кадре объекта. w - ширина Ббокса, всегда одно значение у каждого id.
    #h - высота Ббокса, всегда одно значение у каждого id. class_trajectory - Используется для классификации траектории.
    #radius - Радиус поиска id, если id потерялся из кадра. N14 -используется для проверки. Не важное значение
    #init_posit - центр Ббокса в текущем кадре.



    if cv2.waitKey(10) == 27:  #
        break
        
sock.close()   
#linker.ShutdownTracker() #Сохранение видео
cv2.destroyAllWindows() 

C:\python\platform\Platform_w_one_points3D
initParam...
video_in video_frames/video_20//
video_out ./output/video_frames/video_20//video_frames/video_20.mp4
path_out_for_DM_images ./output/video_frames/video_20//
Running on device: cuda:0
initCaptureObj...
initTracker...
start_ind    1
True
был 1920 1080
стал 640 360
был 1920 1080
стал 640 360
[INFO] Facenet_pytorch took 1.347030 seconds
no init_000: 0
[INFO] Facenet_pytorch took 0.087971 seconds
640 360
[INFO] Facenet_pytorch took 0.073999 seconds
w,h,x,y 25 32 269 27 0.0390625 0.08888888888888889 640 360
w,h,x,y 35 43 398 7 0.0546875 0.11944444444444445 640 360
Sent:{"objects":[]}
[INFO] Facenet_pytorch took 0.075001 seconds
w,h,x,y 25 31 268 27 0.0390625 0.08611111111111111 640 360
w,h,x,y 35 43 398 7 0.0546875 0.11944444444444445 640 360
Sent:{"objects":[]}
[INFO] Facenet_pytorch took 0.086001 seconds
w,h,x,y 25 31 266 29 0.0390625 0.08611111111111111 640 360
w,h,x,y 35 43 398 7 0.0546875 0.11944444444444445 640 360
Sent:{"objects"

[INFO] Facenet_pytorch took 0.074999 seconds
w,h,x,y 25 32 275 27 0.0390625 0.08888888888888889 640 360
w,h,x,y 37 51 400 3 0.0578125 0.14166666666666666 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3396, "y": -0.498, "z": 5.1845, "name": "human"}, { "id": "1", "x": -0.2725, "y": -0.5979, "z": 7.1093, "name": "human"}]}
[INFO] Facenet_pytorch took 0.084970 seconds
w,h,x,y 38 52 400 4 0.059375 0.14444444444444443 640 360
w,h,x,y 25 32 276 27 0.0390625 0.08888888888888889 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3382, "y": -0.4955, "z": 5.1556, "name": "human"}, { "id": "1", "x": -0.2717, "y": -0.5984, "z": 7.1148, "name": "human"}]}
[INFO] Facenet_pytorch took 0.076000 seconds
w,h,x,y 24 31 276 27 0.0375 0.08611111111111111 640 360
w,h,x,y 34 43 400 7 0.053125 0.11944444444444445 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3313, "y": -0.4853, "z": 5.0104, "name": "human"}, { "id": "1", "x": -0.268, "y": -0.6009, "z": 7.147, "name": "human"}]}
[INFO] Facenet_pytorch took 0.074000 se

[INFO] Facenet_pytorch took 0.085999 seconds
w,h,x,y 23 30 282 28 0.0359375 0.08333333333333333 640 360
w,h,x,y 34 43 398 9 0.053125 0.11944444444444445 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3288, "y": -0.484, "z": 5.0537, "name": "human"}, { "id": "1", "x": -0.2496, "y": -0.6009, "z": 7.1605, "name": "human"}]}
[INFO] Facenet_pytorch took 0.076000 seconds
w,h,x,y 25 32 284 28 0.0390625 0.08888888888888889 640 360
w,h,x,y 34 43 398 9 0.053125 0.11944444444444445 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3317, "y": -0.4844, "z": 5.1025, "name": "human"}, { "id": "1", "x": -0.2379, "y": -0.6017, "z": 7.1863, "name": "human"}]}
[INFO] Facenet_pytorch took 0.078000 seconds
w,h,x,y 25 33 285 28 0.0390625 0.09166666666666666 640 360
w,h,x,y 34 43 398 9 0.053125 0.11944444444444445 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3326, "y": -0.4852, "z": 5.1165, "name": "human"}, { "id": "1", "x": -0.2351, "y": -0.6025, "z": 7.1962, "name": "human"}]}
[INFO] Facenet_pytorch took 0.07999

[INFO] Facenet_pytorch took 0.084000 seconds
w,h,x,y 35 43 398 9 0.0546875 0.11944444444444445 640 360
w,h,x,y 23 30 275 26 0.0359375 0.08333333333333333 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3446, "y": -0.4986, "z": 5.3019, "name": "human"}, { "id": "1", "x": -0.2758, "y": -0.6229, "z": 7.3546, "name": "human"}]}
[INFO] Facenet_pytorch took 0.075000 seconds
w,h,x,y 34 42 399 9 0.053125 0.11666666666666667 640 360
w,h,x,y 23 30 275 25 0.0359375 0.08333333333333333 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3231, "y": -0.4737, "z": 4.9626, "name": "human"}, { "id": "1", "x": -0.2795, "y": -0.6354, "z": 7.4539, "name": "human"}]}
[INFO] Facenet_pytorch took 0.074998 seconds
w,h,x,y 34 42 399 8 0.053125 0.11666666666666667 640 360
w,h,x,y 23 30 275 25 0.0359375 0.08333333333333333 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3509, "y": -0.5042, "z": 5.3298, "name": "human"}, { "id": "1", "x": -0.2815, "y": -0.64, "z": 7.507, "name": "human"}]}
[INFO] Facenet_pytorch took 0.073997

w,h,x,y 37 49 401 4 0.0578125 0.1361111111111111 640 360
w,h,x,y 23 30 275 26 0.0359375 0.08333333333333333 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3307, "y": -0.4705, "z": 4.8786, "name": "human"}, { "id": "1", "x": -0.2836, "y": -0.6406, "z": 7.5631, "name": "human"}]}
[INFO] Facenet_pytorch took 0.078000 seconds
w,h,x,y 38 51 402 4 0.059375 0.14166666666666666 640 360
w,h,x,y 23 30 275 25 0.0359375 0.08333333333333333 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3309, "y": -0.4706, "z": 4.8781, "name": "human"}, { "id": "1", "x": -0.2835, "y": -0.6445, "z": 7.56, "name": "human"}]}
[INFO] Facenet_pytorch took 0.067998 seconds
w,h,x,y 38 50 402 5 0.059375 0.1388888888888889 640 360
w,h,x,y 23 30 275 25 0.0359375 0.08333333333333333 640 360
Sent:{"objects":[{ "id": "0", "x": 0.3311, "y": -0.4705, "z": 4.8784, "name": "human"}, { "id": "1", "x": -0.2835, "y": -0.6445, "z": 7.56, "name": "human"}]}
[INFO] Facenet_pytorch took 0.070999 seconds
w,h,x,y 36 47 402 7 0.05625 0.130555555

...

[INFO] Facenet_pytorch took 0.088999 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2868, "y": -0.452, "z": 10.4879, "name": "human"}]}
[INFO] Facenet_pytorch took 0.085000 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2869, "y": -0.4522, "z": 10.4845, "name": "human"}]}
[INFO] Facenet_pytorch took 0.071000 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2872, "y": -0.4516, "z": 10.4442, "name": "human"}]}
[INFO] Facenet_pytorch took 0.073999 seconds
w,h,x,y 17 23 287 101 0.0265625 0.06388888888888888 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2871, "y": -0.4517, "z": 10.4397, "name": "human"}]}
[INFO] Facenet_pytorch took 0.081999 seconds
w,h,x,y 16 21 287 101 0.025 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2873, "y": -0.4522, "z": 10.4458, "name": "human"}]}
[INFO] Facenet_p

[INFO] Facenet_pytorch took 0.078000 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2894, "y": -0.4607, "z": 10.604, "name": "human"}]}
[INFO] Facenet_pytorch took 0.093000 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2899, "y": -0.4612, "z": 10.6138, "name": "human"}]}
[INFO] Facenet_pytorch took 0.082000 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2926, "y": -0.4624, "z": 10.6416, "name": "human"}]}
[INFO] Facenet_pytorch took 0.078000 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2913, "y": -0.4602, "z": 10.5911, "name": "human"}]}
[INFO] Facenet_pytorch took 0.074003 seconds
w,h,x,y 16 22 288 102 0.025 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.289, "y": -0.4603, "z": 10.6072, "name": "human"}]}
[INFO] Facenet_py

[INFO] Facenet_pytorch took 0.094001 seconds
w,h,x,y 16 22 288 102 0.025 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.284, "y": -0.4544, "z": 10.5298, "name": "human"}]}
[INFO] Facenet_pytorch took 0.084000 seconds
w,h,x,y 16 21 288 101 0.025 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2838, "y": -0.4552, "z": 10.561, "name": "human"}]}
[INFO] Facenet_pytorch took 0.080999 seconds
w,h,x,y 16 21 288 101 0.025 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.284, "y": -0.4563, "z": 10.5765, "name": "human"}]}
[INFO] Facenet_pytorch took 0.085998 seconds
w,h,x,y 17 22 287 102 0.0265625 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2849, "y": -0.4564, "z": 10.5841, "name": "human"}]}
[INFO] Facenet_pytorch took 0.091003 seconds
w,h,x,y 17 21 287 101 0.0265625 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2855, "y": -0.4568, "z": 10.5854, "name": "human"}]}
[INFO] Facenet_pytorch took

[INFO] Facenet_pytorch took 0.078619 seconds
w,h,x,y 16 21 288 101 0.025 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2845, "y": -0.4569, "z": 10.5513, "name": "human"}]}
[INFO] Facenet_pytorch took 0.076804 seconds
w,h,x,y 16 22 288 102 0.025 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2846, "y": -0.4571, "z": 10.5636, "name": "human"}]}
[INFO] Facenet_pytorch took 0.085204 seconds
w,h,x,y 16 22 288 102 0.025 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2858, "y": -0.4599, "z": 10.636, "name": "human"}]}
[INFO] Facenet_pytorch took 0.079433 seconds
w,h,x,y 16 22 288 102 0.025 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2856, "y": -0.4596, "z": 10.6383, "name": "human"}]}
[INFO] Facenet_pytorch took 0.083531 seconds
w,h,x,y 16 21 288 101 0.025 0.058333333333333334 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2855, "y": -0.46, "z": 10.64, "name": "human"}]}
[INFO] Facenet_pytorch took 0.074538 s

[INFO] Facenet_pytorch took 0.084520 seconds
w,h,x,y 17 22 287 102 0.0265625 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2865, "y": -0.4522, "z": 10.4577, "name": "human"}]}
[INFO] Facenet_pytorch took 0.099999 seconds
w,h,x,y 17 23 287 101 0.0265625 0.06388888888888888 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2857, "y": -0.4511, "z": 10.4266, "name": "human"}]}
[INFO] Facenet_pytorch took 0.086998 seconds
w,h,x,y 17 23 287 101 0.0265625 0.06388888888888888 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2852, "y": -0.4502, "z": 10.4017, "name": "human"}]}
[INFO] Facenet_pytorch took 0.085999 seconds
w,h,x,y 17 22 287 102 0.0265625 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2848, "y": -0.4492, "z": 10.3855, "name": "human"}]}
[INFO] Facenet_pytorch took 0.095995 seconds
w,h,x,y 17 22 287 102 0.0265625 0.06111111111111111 640 360
Sent:{"objects":[{ "id": "35", "x": -0.2845, "y": -0.4483, "z": 10.372, "name": "human"}]}
[INFO] Facenet_p

In [ ]:
 Sent:{"objects":[{ "id": "0", "x": 1.1879, "y": -0.9447, "z": 4.6334, "name": "human"},
                  { "id": "1", "x": -0.3193, "y": -0.8929, "z": 6.0193, "name": "human"}]}
        
Sent:{"objects":[{ "id": "0", "x": 0.6191, "y": -0.4935, "z": 4.8346, "name": "human"},
                 { "id": "1", "x": -0.1624, "y": -0.4548, "z": 6.1202, "name": "human"}]}